In [1]:
import tensorflow as tf
import pandas as pd
from numpy import array
import nengo
import numpy as np
import nengo_dl
import matplotlib.pyplot as plt
from urllib.request import urlretrieve
from nengo.utils.filter_design import cont2discrete
from sklearn.model_selection import train_test_split

# Utils

In [2]:
# split a univariate sequence into samples
def split_sequence(sequence, n_steps):
	X, y = list(), list()
	for i in range(len(sequence)):
		# find the end of this pattern
		end_ix = i + n_steps
		# check if we are beyond the sequence
		if end_ix > len(sequence)-1:
			break
		# gather input and output parts of the pattern
		seq_x, seq_y = sequence[i:end_ix], sequence[end_ix]
		X.append(seq_x)
		y.append(seq_y)
	return array(X), array(y)

# The Dataset: Dummy Dataset

In [3]:
# taken from https://forum.nengo.ai/t/lmu-for-time-series-forecasting/1821/11

x_dummy_train = array([[[0.16240086],
        [0.13572511],
        [0.12298894]],

       [[0.13573571],
        [0.12298894],
        [0.1394957 ]],

       [[0.12299854],
        [0.1394957 ],
        [0.16518061]],

       [[0.13950658],
        [0.16518061],
        [0.15289813]],

       [[0.1651935 ],
        [0.15289813],
        [0.14116833]],

       [[0.15291007],
        [0.14116833],
        [0.1374616 ]],

       [[0.14117935],
        [0.1374616 ],
        [0.12912672]],

       [[0.13747232],
        [0.12912672],
        [0.11594404]],

       [[0.1291368 ],
        [0.11594404],
        [0.13490303]],

       [[0.11595309],
        [0.13490303],
        [0.13712141]],
                 
       [[0.13491356],
        [0.13712141],
        [0.14390409]],

       [[0.13713211],
        [0.14390409],
        [0.16589645]],

       [[0.14391532],
        [0.16589645],
        [0.15786646]],

       [[0.1659094 ],
        [0.15786646],
        [0.16160157]],

       [[0.15787878],
        [0.16160157],
        [0.14208264]],

       [[0.16161418],
        [0.14208264],
        [0.12267004]],

       [[0.14209373],
        [0.12267004],
        [0.13620001]],

       [[0.12267962],
        [0.13620001],
        [0.11758829]],

       [[0.13621063],
        [0.11758829],
        [0.13591649]],

       [[0.11759747],
        [0.13591649],
        [0.15659777]]])

y_dummy_train = array([[[0.1394957 ]],

               [[0.16518061]],

               [[0.15289813]],

               [[0.14116833]],

               [[0.1374616 ]],

               [[0.12912672]],

               [[0.11594404]],

               [[0.13490303]],

               [[0.13712141]],

               [[0.14390409]],
                 
               [[0.1394957 ]],

               [[0.16518061]],

               [[0.15289813]],

               [[0.14116833]],

               [[0.1374616 ]],

               [[0.12912672]],

               [[0.11594404]],

               [[0.13490303]],

               [[0.13712141]],

               [[0.14390409]]])


x_dummy_test = array([[[0.41645002],
                [0.36998038],
                [0.45262021]],

               [[0.37000926],
                [0.45262021],
                [0.46759614]],

               [[0.45265554],
                [0.46759614],
                [0.46540604]]])


y_dummy_test = array([[[0.46759614]],
                [[0.46540604]],
                [[0.48036778]]])

print(x_dummy_train.shape)
print(y_dummy_train.shape)
print(x_dummy_test.shape)
print(y_dummy_test.shape)
# (20, 3, 1)
# (20, 1, 1)
# (3, 3, 1)
# (3, 1, 1)

(20, 3, 1)
(20, 1, 1)
(3, 3, 1)
(3, 1, 1)


## Model & Training

## Regular LMU Cell

In [4]:
class LMUCellRegular(nengo.Network):
    def __init__(self, units, order, theta, input_d, **kwargs):
        super().__init__(**kwargs)

        # compute the analytically derived weight matrices used in the LMU. 
        # These are determined statically based on the theta/order parameters from above. 
        # It is also possible to optimize these parameters using backpropagation, using a framework such as NengoDL.
        Q = np.arange(order, dtype=np.float64)
        R = (2 * Q + 1)[:, None] / theta
        j, i = np.meshgrid(Q, Q)

        A = np.where(i < j, -1, (-1.0) ** (i - j + 1)) * R
        B = (-1.0) ** Q[:, None] * R
        C = np.ones((1, order))
        D = np.zeros((1,))
        
#       here we are using zero-order hold(zoh) method to 
#       discretize the value of A and B 
        A, B, _, _, _ = cont2discrete((A, B, C, D), dt=1.0, method="zoh")

        with self:
            nengo_dl.configure_settings(trainable=None)

            # create objects corresponding to the x/u/m/h variables in the lmu diagram
            self.x = nengo.Node(size_in=input_d)
            self.u = nengo.Node(size_in=1)
            self.m = nengo.Node(size_in=order)
            self.h = nengo_dl.TensorNode(tf.nn.tanh, shape_in=(units,), pass_time=False)

            # compute u_t from the above diagram. we have removed e_h and e_m as they
            # are not needed in this task.
            nengo.Connection(
                self.x, self.u, transform=np.ones((1, input_d)), synapse=None
            )

            # compute m_t
            # in this implementation we'll make A and B non-trainable, but they
            # could also be optimized in the same way as the other parameters.
            # note that setting synapse=0 (versus synapse=None) adds a one-timestep
            # delay, so we can think of any connections with synapse=0 as representing
            # value_{t-1}.
            conn_A = nengo.Connection(self.m, self.m, transform=A, synapse=0)
            # self.config[conn_A].trainable = False  ---> trying to make conn_A trainable
            conn_B = nengo.Connection(self.u, self.m, transform=B, synapse=None)
            # self.config[conn_B].trainable = False  ---> trying to make conn_B trainable

            # compute h_t
            nengo.Connection(
                self.x, self.h, transform=nengo_dl.dists.Glorot(), synapse=None
            )
            nengo.Connection(
                self.h, self.h, transform=nengo_dl.dists.Glorot(), synapse=0
            )
            nengo.Connection(
                self.m,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )
            

In [5]:
with nengo.Network(seed=10) as net:
    nengo_dl.configure_settings(
        trainable=None,
        stateful=None,
        keep_history=False,
    )

    inp = nengo.Node(np.zeros(x_dummy_train.shape[-1]))

    lmu = LMUCellRegular(
        units=16, # how many neurons
        order=32, # how many legendre polynomials used to orthogonally represent the sliding window
        theta=x_dummy_train.shape[1], # 
        input_d=x_dummy_train.shape[-1], # Dimensionality of input signal.
    )
    
    conn = nengo.Connection(inp, lmu.x, synapse=None)
    net.config[conn].trainable = True 

    out = nengo.Node(size_in=1) #changed to 1
    nengo.Connection(lmu.h, out,transform=nengo_dl.dists.Glorot(), synapse=None)
    
    # record output. note that we set keep_history=False above, so this will
    # only record the output on the last timestep (which is all we need
    # on this task)   
    p = nengo.Probe(out)   

In [6]:
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(learning_rate=0.001),
    )
    
    test_acc = sim.evaluate(x_dummy_test, y_dummy_test, verbose=2)

    
    print("--------------------------------------------------")
    print(f"The test accuracy before training is : {test_acc}")
    print("--------------------------------------------------")
    
    
    output_x = sim.predict(x_dummy_test)    
    print(f"The prediction before training is: {list(output_x.values())[0]}")
    print("--------------------------------------------------")
    
    
    sim.keras_model.summary()
    training_history = sim.fit(x_dummy_train, y_dummy_train, epochs=10)
    
    test_acc = sim.evaluate(x_dummy_test, y_dummy_test, verbose=2)
    
    
    print("--------------------------------------------------")
    print(f"The test accuracy after training is : {test_acc}")
    print("--------------------------------------------------")
    

    output_x = sim.predict(x_dummy_test)
    
    
    # the output is in a dict form, so get the values from the output probe
    # which is the first value of the dictionary
    x_dummy_test_predictions = list(output_x.values())[0]

Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
|###           Constructing graph: build stage (5%)              | ETA: 0:00:00

/Users/davide/Documents/MasterThesis/nengo/.nengoenv/lib/python3.9/site-packages/nengo_dl/simulator.py:460: UserWarning: No GPU support detected. See https://www.nengo.ai/nengo-dl/installation.html#installing-tensorflow for instructions on setting up TensorFlow with GPU support.
  warnings.warn(


Construction finished in 0:00:00                                               
3/3 - 1s - loss: 0.3246 - probe_loss: 0.3246 - 778ms/epoch - 259ms/step        
--------------------------------------------------
The test accuracy before training is : {'loss': 0.32455477118492126, 'probe_loss': 0.32455477118492126}
--------------------------------------------------
The prediction before training is: [[[-0.09751108]]                            

 [[-0.07084166]]

 [[-0.12523648]]]
--------------------------------------------------
Model: "keras_model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 node (InputLayer)              [(1, None, 1)]       0           []                               
                                                                                                  
 n_steps (InputLayer)           [(1, 1)]         

In [9]:
print(f'Predicted values are: {x_dummy_test_predictions.T}')
print(f'True values are: {y_dummy_test.T}')
from sklearn.metrics import mean_squared_error
error = np.sqrt(mean_squared_error(y_dummy_test.reshape(3,1), x_dummy_test_predictions.reshape(3,1)))
print(f'The RMSE error of Regular LMU is {error}')

# results are okeysh

Predicted values are: [[[0.43847373 0.44980425 0.46187845]]]
True values are: [[[0.46759614 0.46540604 0.48036778]]]
The RMSE error of Regular LMU is 0.021858530168903528


# The Dataset: Augmented GAN Fitbit. Univariate One User

In [10]:
fitbit_vanilla = pd.read_csv('../dataset-copy/final-dataset/User10.csv')  # only one users, results were still bad. trying with all the .csv (2 cells below)

In [11]:
fitbit_vanilla

Date Meal_label   Fat  Fiber   Carbs   Sodium  Protein  \
0    2019-02-05  Breakfast  2.40  21.85   57.60   379.32     3.79   
1    2019-02-05      Lunch  9.60  54.14  107.49  2390.36    27.27   
2    2019-02-05     Dinner  6.62   7.03   49.88   195.44    11.83   
3    2019-02-06  Breakfast  2.63   1.88   20.50   139.16     3.39   
4    2019-02-06      Lunch  0.00   0.00    0.00     0.00     0.00   
..          ...        ...   ...    ...     ...      ...      ...   
196  2019-06-04      Lunch  6.34  35.02  130.12   667.20    69.14   
197  2019-06-04     Dinner  5.72  31.93   76.13   924.36    19.15   
198  2019-06-05  Breakfast  2.20  24.75   65.02   475.40    12.01   
199  2019-06-05      Lunch  4.40  45.79   42.30   268.20    86.50   
200  2019-06-05     Dinner  3.13  56.53   65.03   672.31    25.10   

     Calories_burned  Resting_heart_rate  Lightly_active_minutes  \
0            1007.88           69.971199                     200   
1            1130.64           69.971199                     200   
2            1179.19           69.971199                     200   
3            1007.55           70.807733                     184   
4            1295.18           70.807733                     184   
..               ...                 ...                     ...   
196           652.80            0.000000                       0   
197           652.80            0.000000                       0   
198           652.80            0.000000                       0   
199           652.80            0.000000                       0   
200           652.80            0.000000                       0   

     Moderately_active_minutes  Very_active_minutes  Sedentary_minutes  
0                           23                   18                383  
1                           23                   18                383  
2                           23                   18                383  
3                           63                   56                740  
4                           63                   56                740  
..                         ...                  ...                ...  
196                          0                    0               1440  
197                          0                    0               1440  
198                          0                    0               1440  
199                          0                    0               1440  
200                          0                    0               1440  

[201 rows x 13 columns]

In [13]:
import glob

# read the multiple users locally multiple user
# fitbit_gan = pd.concat(map(pd.read_csv, glob.glob('../dataset-copy/GAN-dataset/Generated_Users_Male_Sweden/*.csv'))).drop(columns='Unnamed: 0')
# fitbit_gan

In [14]:
# multiple user from github
fitbit_gan = pd.read_csv('https://raw.githubusercontent.com/cateripa/nengo/main/Combined_Generated_Users_Male_Sweden.csv')

In [15]:
fitbit_gan_numeric = fitbit_gan[['2', '3', '4', '5', '6', '7', '8']]
fitbit_gan_numeric

2          3          4           5          6            7  \
0      1.875985   3.346735  18.267080  240.600805   3.658424   764.564417   
1      4.499530   4.247520  65.778083   82.385594  19.474107  1017.954892   
2      6.682604  11.931909  59.506158  551.814590   7.201182   637.937605   
3      2.459811   0.214387  15.176598    0.000000   0.000000   877.060914   
4      2.134494   6.847388  50.639496  199.970213  20.844487   555.112548   
...         ...        ...        ...         ...        ...          ...   
38695  8.472457   3.879564  95.157633  343.788223  36.877441  1242.926589   
38696  0.000000  15.707265  61.635852  810.987229  16.687693  1347.297748   
38697  1.680398   0.000000  27.668089    0.000000   0.000000   820.262002   
38698  7.180726  12.907930  84.843558  387.350136  25.382101  1236.297722   
38699  1.880300   0.000000  30.045851    0.000000   0.000000  1064.180533   

               8  
0      60.695096  
1      60.695096  
2      60.695096  
3      61.524284  
4      61.524284  
...          ...  
38695  76.716811  
38696  76.716811  
38697  76.646567  
38698  76.646567  
38699  76.646567  

[38700 rows x 7 columns]

In [16]:
# normalized using pandas
fitbit_gan_numeric_pd_scaled = (fitbit_gan_numeric - fitbit_gan_numeric.min()) / (fitbit_gan_numeric.max() - fitbit_gan_numeric.min())
fitbit_gan_numeric_pd_scaled

2         3         4         5         6         7         8
0      0.050432  0.106831  0.093677  0.164445  0.041585  0.144097  0.161625
1      0.120960  0.135585  0.337321  0.056309  0.221360  0.282158  0.161625
2      0.179647  0.380877  0.305158  0.377152  0.081855  0.075104  0.161625
3      0.066126  0.006843  0.077828  0.000000  0.000000  0.205391  0.185374
4      0.057381  0.218575  0.259688  0.136675  0.236936  0.029976  0.185374
...         ...       ...       ...       ...       ...       ...       ...
38695  0.227763  0.123839  0.487985  0.234971  0.419181  0.404735  0.620498
38696  0.000000  0.501389  0.316079  0.554291  0.189687  0.461603  0.620498
38697  0.045174  0.000000  0.141887  0.000000  0.000000  0.174444  0.618486
38698  0.193038  0.412032  0.435093  0.264745  0.288515  0.401124  0.618486
38699  0.050548  0.000000  0.154080  0.000000  0.000000  0.307345  0.618486

[38700 rows x 7 columns]

In [17]:
from sklearn import preprocessing
# normalisation using scikit
scaler = preprocessing.MinMaxScaler()
array_scaled = scaler.fit_transform(fitbit_gan_numeric)
fitbit_gan_sci_scaled = pd.DataFrame(array_scaled, columns=fitbit_gan_numeric.columns, index=fitbit_gan_numeric.index)

fitbit_gan_sci_scaled

# pd and scikit are the same in this case, no bias using minMax scaler

2         3         4         5         6         7         8
0      0.050432  0.106831  0.093677  0.164445  0.041585  0.144097  0.161625
1      0.120960  0.135585  0.337321  0.056309  0.221360  0.282158  0.161625
2      0.179647  0.380877  0.305158  0.377152  0.081855  0.075104  0.161625
3      0.066126  0.006843  0.077828  0.000000  0.000000  0.205391  0.185374
4      0.057381  0.218575  0.259688  0.136675  0.236936  0.029976  0.185374
...         ...       ...       ...       ...       ...       ...       ...
38695  0.227763  0.123839  0.487985  0.234971  0.419181  0.404735  0.620498
38696  0.000000  0.501389  0.316079  0.554291  0.189687  0.461603  0.620498
38697  0.045174  0.000000  0.141887  0.000000  0.000000  0.174444  0.618486
38698  0.193038  0.412032  0.435093  0.264745  0.288515  0.401124  0.618486
38699  0.050548  0.000000  0.154080  0.000000  0.000000  0.307345  0.618486

[38700 rows x 7 columns]

In [18]:
calories_col = array(fitbit_gan_sci_scaled['7'])
calories_col

array([0.14409712, 0.2821583 , 0.07510381, ..., 0.17444425, 0.40112358,
       0.30734459])

In [19]:
# split the sequence
univ_steps = 3
x, y = split_sequence(calories_col, univ_steps)

n_features = 1
x = x.reshape((x.shape[0], x.shape[1], n_features))
y = y.reshape(len(y), 1, -1)

print(x.shape)
print(y.shape)

# split into train and test
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.20)

print("The shape of x, y for train, test")
print(x_train.shape, x_test.shape, y_train.shape, y_test.shape)
print("y train:")
print(y_train)

(38697, 3, 1)
(38697, 1, 1)
The shape of x, y for train, test
(30957, 3, 1) (7740, 3, 1) (30957, 1, 1) (7740, 1, 1)
y train:
[[[0.29264089]]

 [[0.27347502]]

 [[0.41925681]]

 ...

 [[0.06454702]]

 [[0.38098656]]

 [[0.51268939]]]


# Model & Training

## LMU Cell

In [20]:
class LMUCell(nengo.Network):
    def __init__(self, units, order, theta, input_d, **kwargs):
        super().__init__(**kwargs)

        # compute the A and B matrices according to the LMU's mathematical derivation
        # (see the paper for details)
        Q = np.arange(order, dtype=np.float64)
        R = (2 * Q + 1)[:, None] / theta
        j, i = np.meshgrid(Q, Q)

        A = np.where(i < j, -1, (-1.0) ** (i - j + 1)) * R
        B = (-1.0) ** Q[:, None] * R
        C = np.ones((1, order))
        D = np.zeros((1,))

        A, B, _, _, _ = cont2discrete((A, B, C, D), dt=1.0, method="zoh")

        with self:
            nengo_dl.configure_settings(trainable=None)

            # create objects corresponding to the x/u/m/h variables in the above diagram
            self.x = nengo.Node(size_in=input_d)
            self.u = nengo.Node(size_in=1)
            self.m = nengo.Node(size_in=order)
            self.h = nengo_dl.TensorNode(tf.nn.tanh, shape_in=(units,), pass_time=False)

            # compute u_t from the above diagram. we have removed e_h and e_m as they
            # are not needed in this task.
            nengo.Connection(
                self.x, self.u, transform=np.ones((1, input_d)), synapse=None
            )

            # compute m_t
            # in this implementation we'll make A and B non-trainable, but they
            # could also be optimized in the same way as the other parameters.
            # note that setting synapse=0 (versus synapse=None) adds a one-timestep
            # delay, so we can think of any connections with synapse=0 as representing
            # value_{t-1}.
            conn_A = nengo.Connection(self.m, self.m, transform=A, synapse=0)
            # self.config[conn_A].trainable = False
            conn_B = nengo.Connection(self.u, self.m, transform=B, synapse=None)
            # self.config[conn_B].trainable = False

            # compute h_t
            nengo.Connection(
                self.x, self.h, transform=nengo_dl.dists.Glorot(), synapse=None
            )
            nengo.Connection(
                self.h, self.h, transform=nengo_dl.dists.Glorot(), synapse=0
            )
            nengo.Connection(
                self.m,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )

In [25]:
with nengo.Network() as net:
    # remove some unnecessary features to speed up the training
    nengo_dl.configure_settings(
        trainable=None,
        stateful=False,
        keep_history=False,
    )

    # input node
    inp = nengo.Node(np.zeros(x_train.shape[-1]))

    # lmu cell
    lmu = LMUCell(
        units=32,
        order=64,
        theta=x_train.shape[1],
        input_d=x_train.shape[-1],
    )
    conn = nengo.Connection(inp, lmu.x, synapse=None)
    # net.config[conn].trainable = False

    # dense linear readout
    out = nengo.Node(size_in=1) # switched to 1
    nengo.Connection(lmu.h, out, transform=nengo_dl.dists.Glorot(), synapse=None)

    # record output. note that we set keep_history=False above, so this will
    # only record the output on the last timestep (which is all we need
    # on this task)
    p = nengo.Probe(out)

In [ ]:
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(learning_rate=0.001),
    )
    
    

    
    test_acc_before = sim.evaluate(x_test, y_test, verbose=0)    
    print("--------------------------------------------------")
    print(f"The test accuracy before training is : {test_acc_before}")
    print("--------------------------------------------------")
    
    
    initial_prdictions = sim.predict(x_test)
    # the output is in a dict form, so get the values from the output probe
    # which is the first value of the dictionary
    initial_predictions_formatted = list(initial_prdictions.values())[0].T
    print("--------------------------------------------------")
    print(f"The initial prediction is: {initial_predictions_formatted}")
    print("--------------------------------------------------")
    
     
    sim.keras_model.summary()
    training_history = sim.fit(x_train, y_train, epochs=10)
    
    
    test_acc_after = sim.evaluate(x_test, y_test, verbose=0)
    print("--------------------------------------------------")
    print(f"The test accuracy after training is : {test_acc_after}")
    print("--------------------------------------------------")
    

    final_predictions = sim.predict(x_test)
    final_predictions_formatted = list(final_predictions.values())[0].T

Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
Construction finished in 0:00:00                                               
--------------------------------------------------0                            
The test accuracy before training is : {'loss': 0.032702863216400146, 'probe_loss': 0.032702863216400146}
--------------------------------------------------
--------------------------------------------------0                            
The initial prediction is: [[[ 0.20239995  0.10262665  0.19659488 ...  0.04522662 -0.0092551
    0.14609459]]]
--------------------------------------------------
Model: "keras_model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 node (InputLayer)              [(1, None, 1)]       0        

In [ ]:
print(f'Predicted values are: {final_predictions_formatted}')
print(f'True values are: {y_test.T}')
from sklearn.metrics import mean_squared_error
error = np.sqrt(mean_squared_error(y_test.reshape(7740, 1), final_predictions_formatted.reshape(7740, 1)))
print(f'The RMSE error of LMU is {error}')

## Regular LMU Cell